## Chapter 10: Machine Translation
https://nlp100.github.io/en/ch10.html

In this chapter, we train a neural machine translation (NMT) model by using IWSLT’14 English to German translation dataset. For the actual implementation of an NMT model, use the off-the-shelf toolkits such as fairseq, Hugging Face Transformers and OpenNMT-py.

### 90. Data Preprocessing
Download the dataset and obtain training, validation and test data by running this script.

4問目までは、以下を参考に進めた。
https://fairseq.readthedocs.io/en/latest/getting_started.html

前処理全体の流れ
- prepare_mt_data.sh
  - origのデータをpreprocessして、prepにsource言語とtarget言語それぞれのテキストを1文1行形式で出力
- preprocess_91.sh
  - 上記をバイナリ化してdata-binに出力

90では./prepare_mt_data.shを実行し、以下のメッセージが表示された。
```
Data successfully downloaded.
de-en/
de-en/IWSLT14.TED.dev2010.de-en.de.xml
de-en/IWSLT14.TED.dev2010.de-en.en.xml
de-en/IWSLT14.TED.tst2010.de-en.de.xml
de-en/IWSLT14.TED.tst2010.de-en.en.xml
de-en/IWSLT14.TED.tst2011.de-en.de.xml
de-en/IWSLT14.TED.tst2011.de-en.en.xml
de-en/IWSLT14.TED.tst2012.de-en.de.xml
de-en/IWSLT14.TED.tst2012.de-en.en.xml
de-en/IWSLT14.TEDX.dev2012.de-en.de.xml
de-en/IWSLT14.TEDX.dev2012.de-en.en.xml
de-en/README
de-en/train.en
de-en/train.tags.de-en.de
de-en/train.tags.de-en.en

gzip: stdin: unexpected end of file
tar: Unexpected EOF in archive
tar: Unexpected EOF in archive
tar: Error is not recoverable: exiting now
pre-processing train data...
Tokenizer Version 1.1
Language: de
Number of threads: 8

Tokenizer Version 1.1
Language: en
Number of threads: 8

clean-corpus.perl: processing prep/tmp/train.tags.de-en.tok.de & .en to prep/tmp/train.tags.de-en.clean, cutoff 1-50, ratio 1.5
..........(100000)..prep/tmp/train.tags.de-en.tok.en is too short! at mosesdecoder/scripts/training/clean-corpus-n.perl line 96, <E> line 127633.
pre-processing valid/test data...
orig/de-en/IWSLT14.TED.dev2010.de-en.de.xml prep/tmp/IWSLT14.TED.dev2010.de-en.de
Tokenizer Version 1.1
Language: de
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2010.de-en.de.xml prep/tmp/IWSLT14.TED.tst2010.de-en.de
Tokenizer Version 1.1
Language: de
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2011.de-en.de.xml prep/tmp/IWSLT14.TED.tst2011.de-en.de
Tokenizer Version 1.1
Language: de
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2012.de-en.de.xml prep/tmp/IWSLT14.TED.tst2012.de-en.de
Tokenizer Version 1.1
Language: de
Number of threads: 8

orig/de-en/IWSLT14.TEDX.dev2012.de-en.de.xml prep/tmp/IWSLT14.TEDX.dev2012.de-en.de
Tokenizer Version 1.1
Language: de
Number of threads: 8

orig/de-en/IWSLT14.TED.dev2010.de-en.en.xml prep/tmp/IWSLT14.TED.dev2010.de-en.en
Tokenizer Version 1.1
Language: en
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2010.de-en.en.xml prep/tmp/IWSLT14.TED.tst2010.de-en.en
Tokenizer Version 1.1
Language: en
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2011.de-en.en.xml prep/tmp/IWSLT14.TED.tst2011.de-en.en
Tokenizer Version 1.1
Language: en
Number of threads: 8

orig/de-en/IWSLT14.TED.tst2012.de-en.en.xml prep/tmp/IWSLT14.TED.tst2012.de-en.en
Tokenizer Version 1.1
Language: en
Number of threads: 8

orig/de-en/IWSLT14.TEDX.dev2012.de-en.en.xml prep/tmp/IWSLT14.TEDX.dev2012.de-en.en
Tokenizer Version 1.1
Language: en
Number of threads: 8

creating train, valid, test...
```

In [3]:
# 確認
!head prep/train.de-en.de prep/train.de-en.en -n 5

==> prep/train.de-en.de <==
und was menschliche gesundheit ist , kann auch ziemlich kompliziert sein .
und diese zwei zusammen zu bringen , erscheint vielleicht wie eine gewaltige aufgabe . aber was ich ihnen zu sagen versuche ist , dass es trotz dieser komplexität einige einfache themen gibt , von denen ich denke , wenn wir diese verstehen , können wir uns wirklich weiter entwickeln .
und diese einfachen themen sind eigentlich keine komplexen wissenschaftlichen zusammenhänge , sondern tatsachen , die wir alle gut kennen .
und ich werde mit dieser hier anfangen : wenn die mama nicht glücklich ist , ist keiner glücklich .
kennen wir das nicht alle ? das haben wir alle schon erlebt .

==> prep/train.de-en.en <==
and it can be a very complicated thing , what human health is .
and bringing those two together might seem a very daunting task , but what i &apos;m going to try to say is that even in that complexity , there &apos;s some simple themes that i think , if we understand , we can rea

### 91. Training the machine translation model
Use the dataset from the problem 90 and train the machine translation model. The choice of the model architecture is arbitrary (e.g., LSTM-based model, Transformer-based model).


In [12]:
!sh preprocess_91.sh

2022-04-03 11:48:31 | INFO | fairseq_cli.preprocess | Namespace(align_suffix=None, alignfile=None, all_gather_list_size=16384, bf16=False, bpe=None, checkpoint_shard_count=1, checkpoint_suffix='', cpu=False, criterion='cross_entropy', dataset_impl='mmap', destdir='data-bin/iwslt14.tokenized.de-en', empty_cache_freq=0, fp16=False, fp16_init_scale=128, fp16_no_flatten_grads=False, fp16_scale_tolerance=0.0, fp16_scale_window=None, joined_dictionary=False, log_format=None, log_interval=100, lr_scheduler='fixed', memory_efficient_bf16=False, memory_efficient_fp16=False, min_loss_scale=0.0001, model_parallel_size=1, no_progress_bar=False, nwordssrc=-1, nwordstgt=-1, only_source=False, optimizer=None, padding_factor=8, profile=False, quantization_config_path=None, scoring='bleu', seed=1, source_lang='de', srcdict=None, target_lang='en', task='translation', tensorboard_logdir=None, testpref='prep/test.de-en', tgtdict=None, threshold_loss_scale=None, thresholdsrc=0, thresholdtgt=0, tokenizer=No

In [15]:
!mkdir -p checkpoints/fconv

In [1]:
!fairseq-train --help

usage: fairseq-train [-h] [--no-progress-bar] [--log-interval LOG_INTERVAL]
                     [--log-format {json,none,simple,tqdm}]
                     [--tensorboard-logdir TENSORBOARD_LOGDIR] [--seed SEED]
                     [--cpu] [--tpu] [--bf16] [--memory-efficient-bf16]
                     [--fp16] [--memory-efficient-fp16]
                     [--fp16-no-flatten-grads]
                     [--fp16-init-scale FP16_INIT_SCALE]
                     [--fp16-scale-window FP16_SCALE_WINDOW]
                     [--fp16-scale-tolerance FP16_SCALE_TOLERANCE]
                     [--min-loss-scale MIN_LOSS_SCALE]
                     [--threshold-loss-scale THRESHOLD_LOSS_SCALE]
                     [--user-dir USER_DIR]
                     [--empty-cache-freq EMPTY_CACHE_FREQ]
                     [--all-gather-list-size ALL_GATHER_LIST_SIZE]
                     [--model-parallel-size MODEL_PARALLEL_SIZE]
                     [--checkpoint-suffix CHECKPOINT_SUFFIX]
          

In [1]:
!(CUDA_VISIBLE_DEVICES=0 fairseq-train data-bin/iwslt14.tokenized.de-en \
    --optimizer nag --lr 0.25 --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv_iwslt_de_en --save-dir checkpoints/fconv)

2022-04-04 12:06:37 | INFO | fairseq_cli.train | Namespace(all_gather_list_size=16384, arch='fconv_iwslt_de_en', batch_size=None, batch_size_valid=None, best_checkpoint_metric='loss', bf16=False, bpe=None, broadcast_buffers=False, bucket_cap_mb=25, checkpoint_shard_count=1, checkpoint_suffix='', clip_norm=0.1, cpu=False, criterion='cross_entropy', curriculum=0, data='data-bin/iwslt14.tokenized.de-en', data_buffer_size=10, dataset_impl=None, ddp_backend='c10d', decoder_attention='True', decoder_embed_dim=256, decoder_embed_path=None, decoder_layers='[(256, 3)] * 3', decoder_out_embed_dim=256, device_id=0, disable_validation=False, distributed_backend='nccl', distributed_init_method=None, distributed_no_spawn=False, distributed_num_procs=1, distributed_port=-1, distributed_rank=0, distributed_world_size=1, distributed_wrapper='DDP', dropout=0.2, empty_cache_freq=0, encoder_embed_dim=256, encoder_embed_path=None, encoder_layers='[(256, 3)] * 4', eval_bleu=False, eval_bleu_args=None, eval_

In [ ]:
# The above process continues over 6 hours creating nealy 1,000 checkpoint models, so I killed the process. Looking at epoches up to 431, the best loss is gained at epoch 21, so most of the epoches might have been meaningless.
# To detect the point where you can be sure that enough amount of training is done, a parameter "patience" can be used. 

In [2]:
!(CUDA_VISIBLE_DEVICES=0 fairseq-train data-bin/iwslt14.tokenized.de-en \
    --optimizer nag --lr 2 --lr-scheduler inverse_sqrt --patience 8 \
    --clip-norm 0.1 --dropout 0.2 --max-tokens 4000 \
    --arch fconv_iwslt_de_en --save-dir checkpoints/fconv2)
# patienceを設定したことで、early stoppingが実行された。outputのvalid on 'valid' subsetを見ていくと、確かにcheckpoint15以降でlossが改善されていない。この部分の実装の詳細については、以下のコミットを参照
# https://github.com/pytorch/fairseq/commit/1512a0e6213c9a84c5bb1eb918147bd6e96092cd
# また、lr-schedulerを設定したため、lrがだんだん小さくなっていることも確認できる

2022-04-06 10:29:40 | INFO | fairseq.tasks.text_to_speech | Please install tensorboardX: pip install tensorboardX
2022-04-06 10:30:27 | INFO | fairseq_cli.train | {'_name': None, 'common': {'_name': None, 'no_progress_bar': False, 'log_interval': 100, 'log_format': None, 'log_file': None, 'tensorboard_logdir': None, 'wandb_project': None, 'azureml_logging': False, 'seed': 1, 'cpu': False, 'tpu': False, 'bf16': False, 'memory_efficient_bf16': False, 'fp16': False, 'memory_efficient_fp16': False, 'fp16_no_flatten_grads': False, 'fp16_init_scale': 128, 'fp16_scale_window': None, 'fp16_scale_tolerance': 0.0, 'on_cpu_convert_precision': False, 'min_loss_scale': 0.0001, 'threshold_loss_scale': None, 'amp': False, 'amp_batch_retries': 2, 'amp_init_scale': 128, 'amp_scale_window': None, 'user_dir': None, 'empty_cache_freq': 0, 'all_gather_list_size': 16384, 'model_parallel_size': 1, 'quantization_config_path': None, 'profile': False, 'reset_logging': False, 'suppress_crashes': False, 'use_plas

### 92. Translating a text
Use the trained model from the problem 91 and implement the program that translates a given English sentence to a German sentence.



In [1]:
!(CUDA_VISIBLE_DEVICES=0 fairseq-generate data-bin/iwslt14.tokenized.de-en \
    --path checkpoints/fconv/checkpoint_best.pt \
    --batch-size 128 --beam 5)

2022-04-05 10:20:58 | INFO | fairseq_cli.generate | Namespace(all_gather_list_size=16384, batch_size=128, batch_size_valid=128, beam=5, bf16=False, bpe=None, broadcast_buffers=False, bucket_cap_mb=25, checkpoint_shard_count=1, checkpoint_suffix='', constraints=None, cpu=False, criterion='cross_entropy', curriculum=0, data='data-bin/iwslt14.tokenized.de-en', data_buffer_size=10, dataset_impl=None, ddp_backend='c10d', decoding_format=None, device_id=0, disable_validation=False, distributed_backend='nccl', distributed_init_method=None, distributed_no_spawn=False, distributed_port=-1, distributed_rank=0, distributed_world_size=1, distributed_wrapper='DDP', diverse_beam_groups=-1, diverse_beam_strength=0.5, diversity_rate=-1.0, empty_cache_freq=0, eval_bleu=False, eval_bleu_args=None, eval_bleu_detok='space', eval_bleu_detok_args=None, eval_bleu_print_samples=False, eval_bleu_remove_bpe=None, eval_tokenized_bleu=False, fast_stat_sync=False, find_unused_parameters=False, fix_batches_to_gpus=

In [2]:
!(CUDA_VISIBLE_DEVICES=0 fairseq-generate data-bin/iwslt14.tokenized.de-en \
    --path checkpoints/fconv2/checkpoint_best.pt \
    --batch-size 128 --beam 5)
# 原因不明

2022-04-06 13:54:15 | INFO | fairseq_cli.generate | Namespace(all_gather_list_size=16384, batch_size=128, batch_size_valid=128, beam=5, bf16=False, bpe=None, broadcast_buffers=False, bucket_cap_mb=25, checkpoint_shard_count=1, checkpoint_suffix='', constraints=None, cpu=False, criterion='cross_entropy', curriculum=0, data='data-bin/iwslt14.tokenized.de-en', data_buffer_size=10, dataset_impl=None, ddp_backend='c10d', decoding_format=None, device_id=0, disable_validation=False, distributed_backend='nccl', distributed_init_method=None, distributed_no_spawn=False, distributed_port=-1, distributed_rank=0, distributed_world_size=1, distributed_wrapper='DDP', diverse_beam_groups=-1, diverse_beam_strength=0.5, diversity_rate=-1.0, empty_cache_freq=0, eval_bleu=False, eval_bleu_args=None, eval_bleu_detok='space', eval_bleu_detok_args=None, eval_bleu_print_samples=False, eval_bleu_remove_bpe=None, eval_tokenized_bleu=False, fast_stat_sync=False, find_unused_parameters=False, fix_batches_to_gpus=

### 93. BLEU score
Use the trained model from the problem 91 and compute the BLEU score on the test set.


23.37

In [2]:
# Look ath the last line of the output of 93. This value matches the following equation
(53.5 * 29.3 * 17.6 * 10.8) ** (1 / 4)

23.363583548513095

### 94. Beam search
Use the beam search when translating a given sentence with the model from the problem 91. Change the beam width from 1 to 100. Then, plot the change in BLEU score on the graph.



### 95. Subword
Use the subword-based segmentation instead of the word-based segmentation. Repeat the problem 91-94 with the new segmentation.



### 96. Plotting the learning curve
Use tools like TensorBoard and visualize how the training of the machine translation model proceeds. Specifically, visualize the metrics such as the loss and the BLEU score on the training data, and the loss and the BLEU score on the validation data.



### 97. Hyper-parameter search
Change the architecture and/or hyper-parameter of the machine translation model and search for the model that achieves the highest performance on the validation data.



### 98. Domain Adaptation
Evaluate the machine translation model on newstest2014 dataset. To do this, use sacreBLEU toolkit. Then, use News Commentary dataset and improve the performance of the model.



### 99. Translation Server
Build a demo system, in which the user can translate arbitrary text on the Web browser.